In [ ]:
pip install folium geopandas 

In [75]:
import folium
import pandas as pd
import numpy as np
import geopandas as gpd

# make a geojason df for sd
geo_data_file = r'/data/bp-codeathon-team-2/sd.geojson'
with open(geo_data_file, 'r') as jsonFile:
    geo_df=gpd.read_file(jsonFile)
geo_df = geo_df.rename(columns = {"zip":"zipcode"})

# make the data df
data_file = r'/data/bp-codeathon-team-2/2022_sd_genomic_metadata.csv'
data_df = pd.read_csv(data_file)
data_df['zipcode'] = data_df['zipcode'].astype(str)


# create a new df for the plot
# @TODO
# I only do a simple count over the zipcode for now
numCasesSeries = data_df.groupby('zipcode').count().nextclade_pango
numCasesByZip = pd.DataFrame()
numCasesByZip['zipcode'] = [str(i) for i in numCasesSeries.index]
numCasesByZip['numcases'] = numCasesSeries.values
# the most dominant lineage
numCasesByZip['lineage'] = list(data_df.groupby('zipcode')['nextclade_pango'].agg(lambda x:x.value_counts().index[0]))

# for hovering text (number of cases)
geo_df = pd.merge(geo_df, numCasesByZip, on=['zipcode'])
geo_df['numcases'] = geo_df['community'].astype(str) + ', ' + geo_df['numcases'].astype(str) \
                    + ",   " + geo_df['lineage'].astype(str)

# create the initial map
sd_map = folium.Map(location=[32.7157, -117.1611], zoom_start=9)

# create the choropleth map
choropleth = folium.Choropleth(
        geo_data=geo_df,
        name='choropleth',
        data=numCasesByZip,
        columns=['zipcode','numcases'],
        key_on='feature.properties.zipcode',
        fill_color='OrRd',
        fill_opacity=0.7,
        line_opacity=0.8,
        line_color='Blue',
        legend_name='number of cases',
        highlight=True
    ).add_to(sd_map)

# add hover text layer
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['numcases'], labels=False)
)

In [92]:
sd_map.save('choropleth.html')

# from IPython.display import IFrame
# IFrame('choropleth.html', width=800, height=600)

sd_map

In [54]:
ZCTA_data_file = r'/data/bp-codeathon-team-2/ZCTA.geojson'
with open(ZCTA_data_file, 'r') as jsonFile:
    ZCTA_df=gpd.read_file(jsonFile)
    
# ZCTA_df.isnull().sum()

highchol_crudeprev        588
ghlth_crude95ci           588
cholscreen_crude95ci      588
copd_crude95ci            588
colon_screen_crude95ci     99
                         ... 
totalpopulation             0
bpmed_crudeprev           588
checkup_crudeprev         588
kidney_crude95ci          588
geometry                    0
Length: 63, dtype: int64

In [55]:
ZCTA_df.isnull().sum()

highchol_crudeprev        588
ghlth_crude95ci           588
cholscreen_crude95ci      588
copd_crude95ci            588
colon_screen_crude95ci     99
                         ... 
totalpopulation             0
bpmed_crudeprev           588
checkup_crudeprev         588
kidney_crude95ci          588
geometry                    0
Length: 63, dtype: int64